In [1]:
#import libraries
import pandas as pd
import json
import re
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import requests
import warnings
import pprint
warnings.simplefilter('ignore')

In [2]:
url ='https://api.spoonacular.com/recipes/complexSearch?apiKey&query=chicken&addRecipeInformation=True&addRecipeNutrition=True&number=100'
new_response= requests.get(url).json()
#new_response  

{'results': [{'vegetarian': False,
   'vegan': False,
   'glutenFree': True,
   'dairyFree': False,
   'veryHealthy': False,
   'cheap': False,
   'veryPopular': False,
   'sustainable': False,
   'weightWatcherSmartPoints': 1,
   'gaps': 'no',
   'lowFodmap': False,
   'aggregateLikes': 6,
   'spoonacularScore': 39.0,
   'healthScore': 5.0,
   'creditsText': 'Foodista.com – The Cooking Encyclopedia Everyone Can Edit',
   'license': 'CC BY 3.0',
   'sourceName': 'Foodista',
   'pricePerServing': 103.22,
   'id': 637876,
   'title': 'Chicken 65',
   'readyInMinutes': 45,
   'servings': 6,
   'sourceUrl': 'http://www.foodista.com/recipe/G4XPLKBW/chicken-65-chicken-marinaded-in-traditional-indian-spices-and-deep-fried',
   'image': 'https://spoonacular.com/recipeImages/637876-312x231.jpg',
   'imageType': 'jpg',
   'nutrition': {'nutrients': [{'name': 'Calories',
      'amount': 112.66,
      'unit': 'kcal',
      'percentOfDailyNeeds': 5.63},
     {'name': 'Fat', 'amount': 2.73, 'unit': 

In [3]:
recipe4_df=pd.json_normalize(new_response,record_path=['results'])
recipe4_df.head(3)

vegetarian  vegan  glutenFree  dairyFree  veryHealthy  cheap  veryPopular  \
0       False  False        True      False        False  False        False   
1       False  False        True       True        False  False        False   
2       False  False        True      False        False  False        False   

   sustainable  weightWatcherSmartPoints gaps  ...  \
0        False                         1   no  ...   
1        False                        14   no  ...   
2        False                         3   no  ...   

                                nutrition.flavonoids  \
0  [{'name': 'Cyanidin', 'amount': 0.0, 'unit': '...   
1  [{'name': 'Cyanidin', 'amount': 0.0, 'unit': '...   
2  [{'name': 'Cyanidin', 'amount': 0.0, 'unit': '...   

                               nutrition.ingredients  \
0  [{'id': 5062, 'name': 'boneless chicken breast...   
1  [{'id': 1012034, 'name': 'Spice Rub', 'amount'...   
2  [{'id': 19334, 'name': 'brown sugar', 'amount'...   

   nutrition.caloricBreakdown.percentProtein  \
0                                      71.55   
1                                      32.31   
2                                      22.48   

   nutrition.caloricBreakdown.percentFat  \
0                                  24.03   
1                                  59.94   
2                                  47.28   

  nutrition.caloricBreakdown.percentCarbs nutrition.weightPerServing.amount  \
0                                    4.42                               109   
1                                    7.75                               296   
2                                   30.24                                39   

  nutrition.weightPerServing.unit  author  preparationMinutes cookingMinutes  
0                               g     NaN                 NaN            NaN  
1                               g     NaN                 NaN            NaN  
2                               g     NaN                 NaN            NaN  

[3 rows x 44 columns]

In [4]:
recipe4_df.drop(columns=['vegetarian', 'vegan', 'glutenFree', 'dairyFree', 'veryHealthy', 'cheap', 'veryPopular', 'sustainable', 'weightWatcherSmartPoints', 'gaps', 'lowFodmap', 'aggregateLikes', 'spoonacularScore',
                      'healthScore', 'creditsText', 'license', 'sourceName', 'pricePerServing','sourceUrl','imageType','summary','diets', 'occasions','spoonacularSourceUrl','nutrition.properties','nutrition.flavonoids','nutrition.caloricBreakdown.percentProtein','nutrition.caloricBreakdown.percentFat','nutrition.caloricBreakdown.percentCarbs','nutrition.weightPerServing.amount',
                      'nutrition.weightPerServing.unit','preparationMinutes','cookingMinutes','author','nutrition.nutrients','nutrition.ingredients'],inplace=True)
#recipe4_df

In [5]:
#recipe4_df['analyzedInstructions']

# One hot encoding dishType column

In [6]:
recipe4_df['dish']=0
recipe4_df.columns

Index(['id', 'title', 'readyInMinutes', 'servings', 'image', 'cuisines',
       'dishTypes', 'analyzedInstructions', 'dish'],
      dtype='object')

In [7]:
for i in range(0,100):
    item =recipe4_df['dishTypes'][i]
    if len(item)==0:
        recipe4_df.iloc[i,8]=0
        
    else:
        #print(item[0])
        
        if any(x in ['lunch', 'dinner', 'antipasti','side dish','salad'] for x in item):
            #print(f"{i}:lunch")
            recipe4_df.iloc[i,8]=1
        if any(x in ['breakfast', 'bread'] for x in item):
            recipe4_df.iloc[i,8]=0
#recipe4_df

In [8]:
recipe4_df.drop(columns=['dishTypes'],inplace=True)
recipe4_df.head(3)

id          title  readyInMinutes  servings  \
0  637876     Chicken 65              45         6   
1  716342   Chicken Suya              45         1   
2  638420  Chicken Wings              45        30   

                                               image cuisines  \
0  https://spoonacular.com/recipeImages/637876-31...       []   
1  https://spoonacular.com/recipeImages/716342-31...       []   
2  https://spoonacular.com/recipeImages/638420-31...       []   

                                analyzedInstructions  dish  
0  [{'name': '', 'steps': [{'number': 1, 'step': ...     1  
1  [{'name': '', 'steps': [{'number': 1, 'step': ...     1  
2  [{'name': 'For the Chicken Wing Drummettes', '...     1

In [9]:
#Getting ingredients for each recipe
#Ingredients is a list of dictionaries in nutrition key
ingredients_list=[]
recipe_idlist=[]

for recipe in new_response['results']:
    recipe_id =recipe['id']
    ingres=recipe['nutrition']['ingredients']
    ingri_dict={}
    for ingredient_dict in ingres:
        name=ingredient_dict['name']
        amount=ingredient_dict['amount']
        unit=ingredient_dict['unit']
        value=str(round(amount,2))+' '+unit 
        ingri_dict[name]=value
    ingredients_list.append(ingri_dict)
    recipe_idlist.append(recipe_id)    

In [10]:
ingredient_names=[]
for i in range(0,100):
    ingredients=list(ingredients_list[i])
    ingredient_names.append(ingredients)
len(ingredient_names)

100

In [11]:
recipe4_df['ingredients']=ingredients_list

In [12]:
recipe4_df['grocery']=ingredient_names
recipe4_df.head()

id            title  readyInMinutes  servings  \
0  637876       Chicken 65              45         6   
1  716342     Chicken Suya              45         1   
2  638420    Chicken Wings              45        30   
3  638308    Chicken Satay              45         4   
4  638086  Chicken Fingers              30         2   

                                               image cuisines  \
0  https://spoonacular.com/recipeImages/637876-31...       []   
1  https://spoonacular.com/recipeImages/716342-31...       []   
2  https://spoonacular.com/recipeImages/638420-31...       []   
3  https://spoonacular.com/recipeImages/638308-31...       []   
4  https://spoonacular.com/recipeImages/638086-31...       []   

                                analyzedInstructions  dish  \
0  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   
1  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   
2  [{'name': 'For the Chicken Wing Drummettes', '...     1   
3  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   
4  [{'name': '', 'steps': [{'number': 1, 'step': ...     1   

                                         ingredients  \
0  {'boneless chicken breast': '83.33 grams', 'ch...   
1  {'Spice Rub': '1.5 Tablespoons', 'chicken': '1...   
2  {'brown sugar': '0.07 tablespoons', 'chicken d...   
3  {'chicken meat': '125.0 grams', 'chilli powder...   
4  {'cayenne pepper': '0.5 dash', 'chicken breast...   

                                             grocery  
0  [boneless chicken breast, chili powder, ginger...  
1  [Spice Rub, chicken, chilli powder, cooking oi...  
2  [brown sugar, chicken drummettes, garlic powde...  
3  [chicken meat, chilli powder, coconut cream, c...  
4  [cayenne pepper, chicken breasts, cornflakes, ...

# Extracting Instructions

In [13]:
recipe_instructions=recipe4_df[['analyzedInstructions','id']]
#recipe_instructions.head(10)

In [14]:
recipe_inst=[]
for instructions,ids in zip(list(recipe_instructions['analyzedInstructions'].values),list(recipe_instructions['id'].values)):
    #print(instructions,ids)
    #print(instructions[0]['steps'])
    instruct={}
    recipe_step=''
    try:
    #break   
        for no_steps in range(len(instructions[0]['steps'])):
            #print(no_steps)
            recipe_step+=instructions[0]['steps'][no_steps]['step']    
            #break
            #print(recipe_step)
        instruct[ids]=recipe_step
        #print(instruct)
        recipe_inst.append(instruct)
    except:
        pass

In [15]:
instruction_final=pd.DataFrame()
for dict_recipe in recipe_inst:
    df=pd.DataFrame(dict_recipe,index=dict_recipe.keys())
    df.columns=['instructions']
    #print(df)
    #break
    instruction_final=pd.concat([instruction_final,df],ignore_index=False,axis=0)

In [16]:
instruction_final.index.names = ['id']
#instruction_final

In [17]:
recipe4_df=recipe4_df.merge(instruction_final,on='id')
recipe4_df.drop(columns=['analyzedInstructions'],inplace=True)

In [18]:
recipe4_df.head(3)

id          title  readyInMinutes  servings  \
0  637876     Chicken 65              45         6   
1  716342   Chicken Suya              45         1   
2  638420  Chicken Wings              45        30   

                                               image cuisines  dish  \
0  https://spoonacular.com/recipeImages/637876-31...       []     1   
1  https://spoonacular.com/recipeImages/716342-31...       []     1   
2  https://spoonacular.com/recipeImages/638420-31...       []     1   

                                         ingredients  \
0  {'boneless chicken breast': '83.33 grams', 'ch...   
1  {'Spice Rub': '1.5 Tablespoons', 'chicken': '1...   
2  {'brown sugar': '0.07 tablespoons', 'chicken d...   

                                             grocery  \
0  [boneless chicken breast, chili powder, ginger...   
1  [Spice Rub, chicken, chilli powder, cooking oi...   
2  [brown sugar, chicken drummettes, garlic powde...   

                                        instructions  
0  Take a large bowl mix in the ginger and garlic...  
1  Heat the oven to 500 F.Wash and season the chi...  
2  Add chicken into a large glass or stainless st...

In [19]:
#Saving 100 recipes dataframe to a csv
recipe4_df.to_csv('./all_recipes/recipe4.csv',index=False)

In [20]:
#scraping nutrition data

In [21]:
nutri_list =[]
id_list=[]
for recipe in new_response['results']:
    recipe_id =recipe['id']
    nutrients =recipe['nutrition']['nutrients']
    nutri_dict={}
    for nutrient_dict in nutrients:
        name = nutrient_dict['name']
        amount = nutrient_dict['amount']
        unit = nutrient_dict['unit']
        #value = str(round(amount,2))+' '+unit
        key=name+' '+unit
        nutri_dict[key]=amount
    nutri_list.append(nutri_dict)
    id_list.append(recipe_id)

In [22]:
nutrition4_df= pd.DataFrame(nutri_list,index=id_list)
nutrition4_df.index.name='recipe_id'
nutrition4_df.head(3)

Calories kcal  Fat g  Saturated Fat g  Carbohydrates g  \
recipe_id                                                           
637876            112.66   2.73             0.78             1.13   
716342            523.01  34.58             9.73            10.07   
638420             91.06   4.86             1.40             6.99   

           Net Carbohydrates g  Sugar g  Cholesterol mg  Sodium mg  Protein g  \
recipe_id                                                                       
637876                    0.80     0.69           55.07     702.30      18.28   
716342                    7.76     2.66          163.29     383.52      41.95   
638420                    6.82     6.67           21.13     275.71       5.20   

           Vitamin B3 mg  ...  Iron mg  Calcium mg  Manganese mg  Copper mg  \
recipe_id                 ...                                                 
637876              8.81  ...     0.51        23.8          0.04       0.03   
716342             15.28  ...     4.54       103.5          0.56       0.20   
638420              1.63  ...     0.42         NaN           NaN        NaN   

           Fiber g  Vitamin C mg  Folate µg  Vitamin K µg  Vitamin D µg  \
recipe_id                                                                 
637876        0.33          1.10       4.55          1.16           NaN   
716342        2.31          8.29      32.35         54.64          0.44   
638420         NaN           NaN        NaN           NaN           NaN   

           Alcohol g  
recipe_id             
637876           NaN  
716342           NaN  
638420           NaN  

[3 rows x 32 columns]

In [23]:
print(nutrition4_df.duplicated().sum())

0


In [24]:
#saving the nutrition details of 100 recipes dataframe to csv
nutrition4_df.to_csv('./all_nutrition/nutrition4.csv',index=True)

In [25]:
#Defining dataframe for ingredients
ingres4_df=pd.DataFrame(ingredients_list,index= recipe_idlist)
ingres4_df.fillna(value=0,inplace=True)
ingres4_df.index.name='recipe_id'
ingres4_df.head(3)

boneless chicken breast chili powder ginger garlic paste  \
recipe_id                                                            
637876                83.33 grams     0.33 tsp           0.67 tbsp   
716342                          0            0                   0   
638420                          0            0                   0   

                  salt turmeric powder            yogurt        Spice Rub  \
recipe_id                                                                   
637876       0.08 tbsp        0.04 tsp         0.67 tbsp                0   
716342     1.0 serving               0                 0  1.5 Tablespoons   
638420               0               0  0.07 tablespoons                0   

             chicken chilli powder cooking oil  ... EVOO coriander powder  \
recipe_id                                       ...                         
637876             0             0           0  ...    0                0   
716342     1.0 pound  1.0 teaspoon        1.0   ...    0                0   
638420             0             0           0  ...    0                0   

          ground almond poppy seeds raisins catsup chicken pieces dry mustard  \
recipe_id                                                                       
637876                0           0       0      0              0           0   
716342                0           0       0      0              0           0   
638420                0           0       0      0              0           0   

          fresh sage leaves wonton wrappers  
recipe_id                                    
637876                    0               0  
716342                    0               0  
638420                    0               0  

[3 rows x 450 columns]

In [26]:
#saving the ingredients of 100 recipes dataframe to csv
ingres4_df.to_csv('./all_ingredients/ingredients4.csv',index=True)